In [1]:
import numpy as np
import pandas as pd
import copy

import torch
from torch.utils.data import TensorDataset, DataLoader
from sklearn.preprocessing import MinMaxScaler

from data import fetch_dataset
from util import move_sliding_window, num_params

from model import LSTMModel
from algorithm import fedgkd

pd.set_option('display.max_columns', None)
pd.set_option('display.max_columns', None)
np.set_printoptions(suppress=True, floatmode='fixed')

In [2]:
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('running on gpu')
else:
    device = torch.device("cpu")

running on gpu


# Parameters

In [3]:
window_size = 90 # Define window_size period and split inputs/labels\
batch_size = 1024
label_col_index = 0

# seq_len = 90  # (timestamps)
hidden_dim = 50
n_layers = 2
lr = 0.0001
output_dim = 1

#fed train params
num_local_epochs = 1
max_rounds = 100 #nb of total rounds for training

kd_weight = 1
buffer_size = 5

# Data Preperation

In [4]:
dataframes = fetch_dataset("./heterog")

Floor0
Floor1
Floor10
Floor11
Floor12
Floor13
Floor14
Floor15
Floor16
Floor17
Floor18
Floor19
Floor2
Floor20
Floor21
Floor22
Floor23
Floor24
Floor25
Floor26
Floor27
Floor28
Floor29
Floor3
Floor30
Floor31
Floor32
Floor33
Floor34
Floor35
Floor36
Floor37
Floor38
Floor39
Floor4
Floor40
Floor41
Floor42
Floor43
Floor44
Floor45
Floor46
Floor47
Floor48
Floor49
Floor5
Floor50
Floor51
Floor52
Floor53
Floor54
Floor55
Floor56
Floor57
Floor58
Floor59
Floor6
Floor60
Floor61
Floor62
Floor63
Floor64
Floor65
Floor66
Floor67
Floor68
Floor69
Floor7
Floor70
Floor71
Floor72
Floor73
Floor74
Floor75
Floor76
Floor77
Floor78
Floor79
Floor8
Floor80
Floor81
Floor82
Floor83
Floor84
Floor85
Floor86
Floor87
Floor88
Floor89
Floor9


In [5]:
n_clients = len(dataframes) #total number of clients to partition data into

In [6]:
for _, df in dataframes.items():
    print(df.columns)
    print(df.shape)

Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(68183, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(58618, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(46840, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(65390, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(57176, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(51707, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(47453, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
 

# Build the training set

In [7]:
train_loader = []
test_loader = []
label_scalers = []
for _, df in dataframes.items():
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

# LSTM model

In [8]:
lstm = LSTMModel(input_dim, hidden_dim, output_dim, n_layers)
model_type = 'LSTM'
print(lstm)
print(num_params(lstm))

LSTMModel(
  (lstm): LSTM(9, 50, num_layers=2, batch_first=True)
  (fc): Linear(in_features=50, out_features=1, bias=True)
  (tanh): Tanh()
)
32651


# Fedgkd

## 10

In [11]:
%%time
lstm_K5_gkd = copy.deepcopy(lstm)
outputs_gkd, targets_gkd, loss_gkd, smape_gkd, mae_gkd, rmse_gkd = fedgkd(
    global_model = lstm_K5_gkd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)


Starting round 0
clients:  [0 1 2 3 4 5 6 7 8 9]
round 0, starting client 1/10, id: 0
Epoch [1/1], Train Loss: 0.11530682275880058
round 0, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.10455583449867037
round 0, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.06750018669602773
round 0, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.06747789967518585
round 0, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.10060089190558691
round 0, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.11614047625177618
round 0, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.09180417799569193
round 0, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.08722466029799904
round 0, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.09982144526309442
round 0, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.09847688259712109
calc smape: 79.10673512482533%
MAE: 13.231847545984238
RMSE: 24.772498770386107
Average Loss:  0.07012003242008416

Starting roun

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06302288139484964
round 1, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.05305874904410707
round 1, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.033449607978885375
round 1, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.03473621635482861
round 1, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.052156055436992046
round 1, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.05969107941397139
round 1, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.04788267014032982
round 1, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.04637908602419953
round 1, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.04955053834451571
round 1, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.05052964622154831
calc smape: 58.853728843736775%
MAE: 13.781090177374269
RMSE: 18.962225754202755
Average Loss:  0.04181556082819855

Starting round 2
clients:  [0 1 2 3 4 5 6 7 8 9]
round 2, starting client 1/10, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04437025379881544
round 2, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.03792104327844249
round 2, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.028001119654315215
round 2, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.029842813666432332
round 2, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.037633146727230504
round 2, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.03952909311329998
round 2, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.03605718118079166
round 2, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.035706791381996415
round 2, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.03454851876530383
round 2, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.03632697206921876
calc smape: 57.67438230909547%
MAE: 13.044087473186718
RMSE: 17.482037305690902
Average Loss:  0.03587171777698141

Starting round 3
clients:  [0 1 2 3 4 5 6 7 8 9]
round 3, starting client 1/10, id: 0


...

Epoch [1/1], Train Loss: 0.0020181576343569554
round 97, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.0021596790925185716
round 97, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.0023718006608154
round 97, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.003107961682149043
round 97, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.002075745369216836
round 97, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.002146160923812941
round 97, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.0023501545346857225
round 97, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.002635473797384363
round 97, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.0017871729990777871
round 97, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.002231495727755828
calc smape: 28.153409498011825%
MAE: 1.9698847606464542
RMSE: 4.674688355663651
Average Loss:  0.0027250082392664358

Starting round 98
clients:  [0 1 2 3 4 5 6 7 8 9]
round 98, starting client 1

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.002015831408020601
round 98, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.0021570594657936864
round 98, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.0023675243088897933
round 98, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.0031052778761547334
round 98, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.0020902765114087516
round 98, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.0021449720905464447
round 98, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.0023464009728025085
round 98, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.0026315288817456276
round 98, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.001786224443801782
round 98, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.002231433483151098
calc smape: 28.21042097811944%
MAE: 1.971669267704309
RMSE: 4.672399818026029
Average Loss:  0.0027216199777607116

Starting round 99
clients:  [0 1 2 3 4 5 6 7 8 9]
round 99, starting clien

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.002011997398990646
round 99, starting client 2/10, id: 1
Epoch [1/1], Train Loss: 0.0021536985541590384
round 99, starting client 3/10, id: 2
Epoch [1/1], Train Loss: 0.002362230785365682
round 99, starting client 4/10, id: 3
Epoch [1/1], Train Loss: 0.0030985326380827106
round 99, starting client 5/10, id: 4
Epoch [1/1], Train Loss: 0.0020500649903935
round 99, starting client 6/10, id: 5
Epoch [1/1], Train Loss: 0.002141131025210426
round 99, starting client 7/10, id: 6
Epoch [1/1], Train Loss: 0.002343993018470467
round 99, starting client 8/10, id: 7
Epoch [1/1], Train Loss: 0.0026277028462992832
round 99, starting client 9/10, id: 8
Epoch [1/1], Train Loss: 0.0017833286760530129
round 99, starting client 10/10, id: 9
Epoch [1/1], Train Loss: 0.002223685526890526
calc smape: 27.834266344397008%
MAE: 1.9699123598482204
RMSE: 4.669269397381241
Average Loss:  0.002715727923579338
CPU times: total: 1h 54min 3s
Wall time: 1h 54min 20s


In [13]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd)

## 20

In [ ]:
%%time
lstm_K5_gkd1 = copy.deepcopy(lstm)
outputs_gkd1, targets_gkd1, loss_gkd1, smape_gkd1, mae_gkd1, rmse_gkd1 = fedgkd(
    global_model = lstm_K5_gkd1,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)

In [ ]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd1, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd1, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd1)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd1)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd1)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd1)

## 30 

In [9]:
%%time
lstm_K5_gkd = copy.deepcopy(lstm)
outputs_gkd, targets_gkd, loss_gkd, smape_gkd, mae_gkd, rmse_gkd = fedgkd(
    global_model = lstm_K5_gkd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)


Starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 0, starting client 1/30, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.07103297247920397
round 0, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.06010420053369469
round 0, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.05074670839692568
round 0, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.05495537028593175
round 0, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.064653138122098
round 0, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.05709050968289375
round 0, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.07066407749379003
round 0, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.057284646439102443
round 0, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.060149295148081504
round 0, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.05083062208292109
round 0, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.0711130970157683
round 0, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.04492264802224541
round 0, starting client 13/30, id: 12
Epoch [1/1

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.053519939792887224
round 1, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.04420967019266553
round 1, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.03904597228392958
round 1, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.043812655642920854
round 1, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.047701828774403425
round 1, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.0432062555802986
round 1, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.05153063095703318
round 1, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.04139417248233311
round 1, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.047108710886767276
round 1, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.03818945724655081
round 1, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.05373365773508946
round 1, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.03381813797903689
round 1, starting client 13/30, id: 12
Epoch 

...

Epoch [1/1], Train Loss: 0.0020439996074375537
round 97, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.0021453519144819847
round 97, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.002408947503782757
round 97, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.0025818365758431016
round 97, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.002312034199183638
round 97, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.002287840632197913
round 97, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.0021514085001891124
round 97, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.0016039574072907136
round 97, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.0028869044304323885
round 97, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.00212360220245534
round 97, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.0024817644734866917
round 97, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.002205164343314735
round 97, starting 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020397613516938435
round 98, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.002141635096631944
round 98, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.002404267165628779
round 98, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.0025769741064412335
round 98, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.0023076280512296676
round 98, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.0022833160313894037
round 98, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.0021477419115300913
round 98, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.0016010766563374762
round 98, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.002880160956500241
round 98, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.0021197305252792795
round 98, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.0024760483768962636
round 98, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.002202250873731253
round 98, startin

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.002035688948795586
round 99, starting client 2/30, id: 1
Epoch [1/1], Train Loss: 0.0021379886104518344
round 99, starting client 3/30, id: 2
Epoch [1/1], Train Loss: 0.002399503736038848
round 99, starting client 4/30, id: 3
Epoch [1/1], Train Loss: 0.0025720675829706678
round 99, starting client 5/30, id: 4
Epoch [1/1], Train Loss: 0.0023031395711851387
round 99, starting client 6/30, id: 5
Epoch [1/1], Train Loss: 0.002278787690738682
round 99, starting client 7/30, id: 6
Epoch [1/1], Train Loss: 0.0021438799496438054
round 99, starting client 8/30, id: 7
Epoch [1/1], Train Loss: 0.0015985084607547041
round 99, starting client 9/30, id: 8
Epoch [1/1], Train Loss: 0.0028736168258966742
round 99, starting client 10/30, id: 9
Epoch [1/1], Train Loss: 0.002116060750806893
round 99, starting client 11/30, id: 10
Epoch [1/1], Train Loss: 0.0024699557531372798
round 99, starting client 12/30, id: 11
Epoch [1/1], Train Loss: 0.002199147009952483
round 99, starting

In [10]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd)

## 40

In [9]:
%%time
lstm_K5_gkd = copy.deepcopy(lstm)
outputs_gkd, targets_gkd, loss_gkd, smape_gkd, mae_gkd, rmse_gkd = fedgkd(
    global_model = lstm_K5_gkd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)


Starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 0, starting client 1/40, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.10189788261393329
round 0, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.09007417613433467
round 0, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.0763311151208149
round 0, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.0793763863689759
round 0, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.09531183024360373
round 0, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.08449962176382544
round 0, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.10295307857764732
round 0, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.08732771388483498
round 0, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.08639768156437921
round 0, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.07660376261574801
round 0, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.10195435505981248
round 0, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.06952806498463217
round 0, starting client 13/40, id: 12
Epoch [1/1]

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06586989665509393
round 1, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.05541693785538276
round 1, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.04711025122863551
round 1, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.05121318732990937
round 1, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.0595971088517796
round 1, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.05330069903284311
round 1, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.06591766614567592
round 1, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.05232626740943709
round 1, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.055523707388112194
round 1, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.046371209883579484
round 1, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.06536885653622446
round 1, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.04138889359800439
round 1, starting client 13/40, id: 12
Epoch [1

...

Epoch [1/1], Train Loss: 0.0019342380170578595
round 97, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.0020365366802757813
round 97, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.002344060652022663
round 97, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.00243569424663506
round 97, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.0021677211771020666
round 97, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.0021334051460144107
round 97, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.0020416253529539382
round 97, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.001551903042951072
round 97, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.0027230613688096557
round 97, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.0020047205430778893
round 97, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.002311184586384721
round 97, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.0021126402425579722
round 97, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019299819091343723
round 98, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.0020316580970150735
round 98, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.0023371793536676295
round 98, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.0024297746873058962
round 98, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.0021621249126672583
round 98, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.002126537972071674
round 98, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.002035733973104004
round 98, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.0015489914254636832
round 98, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.0027147923493220545
round 98, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.0020000958713892575
round 98, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.002304525792472607
round 98, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.0021076130797155197
round 98, starti

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019254078846951972
round 99, starting client 2/40, id: 1
Epoch [1/1], Train Loss: 0.0020264398772269487
round 99, starting client 3/40, id: 2
Epoch [1/1], Train Loss: 0.0023299023547830684
round 99, starting client 4/40, id: 3
Epoch [1/1], Train Loss: 0.0024238086417408696
round 99, starting client 5/40, id: 4
Epoch [1/1], Train Loss: 0.0021563902687789364
round 99, starting client 6/40, id: 5
Epoch [1/1], Train Loss: 0.0021199815484578724
round 99, starting client 7/40, id: 6
Epoch [1/1], Train Loss: 0.002028722821017475
round 99, starting client 8/40, id: 7
Epoch [1/1], Train Loss: 0.0015462933510172897
round 99, starting client 9/40, id: 8
Epoch [1/1], Train Loss: 0.0027063301755473586
round 99, starting client 10/40, id: 9
Epoch [1/1], Train Loss: 0.0019953316056031596
round 99, starting client 11/40, id: 10
Epoch [1/1], Train Loss: 0.0022976205497495057
round 99, starting client 12/40, id: 11
Epoch [1/1], Train Loss: 0.0021021947981544617
round 99, star

In [10]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd)

## 50

In [16]:
%%time
lstm_K5_gkd = copy.deepcopy(lstm)
outputs_gkd, targets_gkd, loss_gkd, smape_gkd, mae_gkd, rmse_gkd = fedgkd(
    global_model = lstm_K5_gkd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)


Starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 0, starting client 1/50, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.059970703432863634
round 0, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.049768722264303115
round 0, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.04274066911441171
round 0, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.047868265679069585
round 0, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.05378093845634299
round 0, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.048054794990457596
round 0, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.058344902168657335
round 0, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.04689386954425641
round 0, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.051968556900437064
round 0, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.04255048882354187
round 0, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.060084566357545555
round 0, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.037352246036262894
round 0, starting client 13/50, id: 12
E

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.04739276692271232
round 1, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.03940461942305167
round 1, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.03620463956354393
round 1, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.04000238186734564
round 1, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.04249108536168933
round 1, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.03911132477223874
round 1, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.045768305457927094
round 1, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.03629697528931329
round 1, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.04271177116494911
round 1, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.03353318361634458
round 1, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.04810525275145966
round 1, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.030531322289454318
round 1, starting client 13/50, id: 12
Epoch [

...

Epoch [1/1], Train Loss: 0.0018504508798458737
round 97, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.0019036581688043142
round 97, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.002215298526506457
round 97, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.002291762773358427
round 97, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.0020385167669949382
round 97, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.0020121351204579695
round 97, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0019192175429968816
round 97, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.001481171683100808
round 97, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.0025506394180970704
round 97, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.001905837963190775
round 97, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.002194162293259675
round 97, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.00198827573484251
round 97, starting c

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0018447235639576075
round 98, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.0018971644801139417
round 98, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.002208452320903436
round 98, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.0022838501335012123
round 98, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.002031323865098371
round 98, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.0020051989704370503
round 98, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0019119361783629535
round 98, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.0014770488355765642
round 98, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.0025414488627575342
round 98, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0018994196121908575
round 98, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.002185848881102478
round 98, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.0019817419754537316
round 98, starti

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0018387700141108824
round 99, starting client 2/50, id: 1
Epoch [1/1], Train Loss: 0.0018907888954143141
round 99, starting client 3/50, id: 2
Epoch [1/1], Train Loss: 0.0022016242000972856
round 99, starting client 4/50, id: 3
Epoch [1/1], Train Loss: 0.0022758334251942445
round 99, starting client 5/50, id: 4
Epoch [1/1], Train Loss: 0.0020240035572152756
round 99, starting client 6/50, id: 5
Epoch [1/1], Train Loss: 0.0019983961123216432
round 99, starting client 7/50, id: 6
Epoch [1/1], Train Loss: 0.0019050109124666935
round 99, starting client 8/50, id: 7
Epoch [1/1], Train Loss: 0.0014730044091471803
round 99, starting client 9/50, id: 8
Epoch [1/1], Train Loss: 0.002532161331216159
round 99, starting client 10/50, id: 9
Epoch [1/1], Train Loss: 0.0018928762276320607
round 99, starting client 11/50, id: 10
Epoch [1/1], Train Loss: 0.0021776500992321726
round 99, starting client 12/50, id: 11
Epoch [1/1], Train Loss: 0.0019754812973061284
round 99, star

In [17]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd)

## 60

In [23]:
%%time
lstm_K5_gkd = copy.deepcopy(lstm)
outputs_gkd, targets_gkd, loss_gkd, smape_gkd, mae_gkd, rmse_gkd = fedgkd(
    global_model = lstm_K5_gkd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)


Starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 0, starting client 1/60, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06293151966946305
round 0, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.05225773952487442
round 0, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.044525981182232485
round 0, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.04998944946290815
round 0, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.056293670088052736
round 0, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.05028263782151044
round 0, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.06097841494389482
round 0, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.04943877465601236
round 0, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.054141311655537434
round 0, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.04467479205103936
round 0, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.0626836964317287
round 0, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.03874479268530481
round 0, starting client 13/60, id: 12
Epoch [

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.05193348429253642
round 1, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.043554203750358685
round 1, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.03951497831278377
round 1, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.044288983641594074
round 1, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.0465113184922798
round 1, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.043096959590911865
round 1, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.05016623749523551
round 1, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.0402294830682705
round 1, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.046494747476222405
round 1, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.037206078638081196
round 1, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.05220422350491086
round 1, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.03334403209584324
round 1, starting client 13/60, id: 12
Epoch 

...

Epoch [1/1], Train Loss: 0.0020795672393913544
round 97, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.002163792530255806
round 97, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.002474202075973153
round 97, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.002618730248536403
round 97, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.0023316577770112253
round 97, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.0023092213683412414
round 97, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.0021785187324181803
round 97, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.001627639769071291
round 97, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.0029077347034427263
round 97, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.0021509300080382403
round 97, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.0024635199079057197
round 97, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.002232181412278135
round 97, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020778909603458885
round 98, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.0021614285211803185
round 98, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.002471867832355201
round 98, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.0026167818121429457
round 98, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.0023293791177407415
round 98, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.0023067108966642992
round 98, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.002176311041694135
round 98, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.0016262873124225801
round 98, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.0029041787593786666
round 98, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.0021490393795560252
round 98, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.0024607479972473816
round 98, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.0022302698527805896
round 98, start

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020761983436180884
round 99, starting client 2/60, id: 1
Epoch [1/1], Train Loss: 0.0021591290656942878
round 99, starting client 3/60, id: 2
Epoch [1/1], Train Loss: 0.0024695763503485876
round 99, starting client 4/60, id: 3
Epoch [1/1], Train Loss: 0.0026147550248139194
round 99, starting client 5/60, id: 4
Epoch [1/1], Train Loss: 0.002327157806245271
round 99, starting client 6/60, id: 5
Epoch [1/1], Train Loss: 0.0023044899571686987
round 99, starting client 7/60, id: 6
Epoch [1/1], Train Loss: 0.0021745607546354473
round 99, starting client 8/60, id: 7
Epoch [1/1], Train Loss: 0.001625261596241474
round 99, starting client 9/60, id: 8
Epoch [1/1], Train Loss: 0.0029008778835234875
round 99, starting client 10/60, id: 9
Epoch [1/1], Train Loss: 0.0021470397769007827
round 99, starting client 11/60, id: 10
Epoch [1/1], Train Loss: 0.0024580134728845824
round 99, starting client 12/60, id: 11
Epoch [1/1], Train Loss: 0.002228192240612483
round 99, starti

In [24]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd)

## 70

In [9]:
%%time
lstm_K5_gkd = copy.deepcopy(lstm)
outputs_gkd, targets_gkd, loss_gkd, smape_gkd, mae_gkd, rmse_gkd = fedgkd(
    global_model = lstm_K5_gkd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)


Starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 0, starting client 1/70, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0852160440793015
round 0, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.07435733141998449
round 0, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.06308289048158461
round 0, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.06546033356411785
round 0, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.07919447809796437
round 0, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.07024400355294345
round 0, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.08647084216008318
round 0, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.07075970521513021
round 0, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.07189218008604188
round 0, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.06216304455193932
round 0, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.08547141853099069
round 0, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.0560344916915423
round 0, starting client 13/70, id: 12
Epoch [1/1]

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.054906203147937656
round 1, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.04554954291217857
round 1, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.03952430351637304
round 1, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.04449401286375872
round 1, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.04873818493532863
round 1, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.044522881973534816
round 1, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.0532546376155035
round 1, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.04240479531153193
round 1, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.04777021863712713
round 1, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.039080758613568765
round 1, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.05426348897162825
round 1, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.0341755180668674
round 1, starting client 13/70, id: 12
Epoch [1

...

Epoch [1/1], Train Loss: 0.0019229422488144402
round 97, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.001995988798120783
round 97, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.002267163062545781
round 97, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.002449454844691882
round 97, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.002153202375418253
round 97, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.00212391258100979
round 97, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.0020413702256297946
round 97, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0015211529296137534
round 97, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.0026620728514479613
round 97, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.0019963215961103778
round 97, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.0022850129874617173
round 97, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.0020747535454574972
round 97, starting 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019183064633013925
round 98, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.001989401629867239
round 98, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.002262300930548614
round 98, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.0024421638740664896
round 98, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.0021460295168005614
round 98, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.002117224093672121
round 98, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.002036135061644018
round 98, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0015174084423188962
round 98, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.002653618514439306
round 98, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.001990335244853567
round 98, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.002277807647866818
round 98, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.0020686503389458124
round 98, starting c

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001913092779500832
round 99, starting client 2/70, id: 1
Epoch [1/1], Train Loss: 0.0019811172646263405
round 99, starting client 3/70, id: 2
Epoch [1/1], Train Loss: 0.002255661229557719
round 99, starting client 4/70, id: 3
Epoch [1/1], Train Loss: 0.0024348357772253737
round 99, starting client 5/70, id: 4
Epoch [1/1], Train Loss: 0.002138657945165918
round 99, starting client 6/70, id: 5
Epoch [1/1], Train Loss: 0.002110844646085752
round 99, starting client 7/70, id: 6
Epoch [1/1], Train Loss: 0.0020314796632659197
round 99, starting client 8/70, id: 7
Epoch [1/1], Train Loss: 0.0015141353865575817
round 99, starting client 9/70, id: 8
Epoch [1/1], Train Loss: 0.0026456537083364446
round 99, starting client 10/70, id: 9
Epoch [1/1], Train Loss: 0.001983917265735929
round 99, starting client 11/70, id: 10
Epoch [1/1], Train Loss: 0.002271086638453804
round 99, starting client 12/70, id: 11
Epoch [1/1], Train Loss: 0.002062591393233129
round 99, starting c

In [10]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd)

## 80

In [16]:
%%time
lstm_K5_gkd = copy.deepcopy(lstm)
outputs_gkd, targets_gkd, loss_gkd, smape_gkd, mae_gkd, rmse_gkd = fedgkd(
    global_model = lstm_K5_gkd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)


Starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 0, starting client 1/80, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.08606265446628039
round 0, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.07456423044204713
round 0, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.06320503110893898
round 0, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.0659652514492764
round 0, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.07974831946194172
round 0, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0704090758692473
round 0, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.08673038001398785
round 0, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.07112592880455954
round 0, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.07275389822629781
round 0, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.06278037848985858
round 0, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.08652508639109631
round 0, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.05595598644331881
round 0, starting client 13/80, id: 12
Epoch [1/1]

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06146645995805848
round 1, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.05115118577248521
round 1, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.044375337117041155
round 1, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.049911901062610106
round 1, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.05493691614405676
round 1, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0497871027328074
round 1, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.05937142091224325
round 1, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.04792525935566649
round 1, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.05372926123583547
round 1, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.04428726424359612
round 1, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.061307727980116994
round 1, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.03867231515285215
round 1, starting client 13/80, id: 12
Epoch [

...

Epoch [1/1], Train Loss: 0.002002133941168036
round 97, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0021301379944715236
round 97, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.0022998483424695837
round 97, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.0025422606553297993
round 97, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.0022805491039021453
round 97, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0022261932783294467
round 97, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.002115339462368472
round 97, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.001577219355825054
round 97, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.0028335407192711364
round 97, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.0021068441376512594
round 97, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.002390084438957275
round 97, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.0022075383887185077
round 97, startin

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0019976245865383933
round 98, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.0021266103088338345
round 98, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.002294337860399133
round 98, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.002536269826997145
round 98, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.0022759048866150392
round 98, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0022204428634722715
round 98, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.002110124066962886
round 98, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.0015737464857937874
round 98, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.0028265591524989134
round 98, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.002101728448501994
round 98, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.002384671141044237
round 98, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.002203549929330811
round 98, starting 

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.001993490888227551
round 99, starting client 2/80, id: 1
Epoch [1/1], Train Loss: 0.002122419163222528
round 99, starting client 3/80, id: 2
Epoch [1/1], Train Loss: 0.0022874159573499724
round 99, starting client 4/80, id: 3
Epoch [1/1], Train Loss: 0.0025298787776252946
round 99, starting client 5/80, id: 4
Epoch [1/1], Train Loss: 0.002270683488776822
round 99, starting client 6/80, id: 5
Epoch [1/1], Train Loss: 0.0022147024268633687
round 99, starting client 7/80, id: 6
Epoch [1/1], Train Loss: 0.0021056392028726435
round 99, starting client 8/80, id: 7
Epoch [1/1], Train Loss: 0.0015708130124279843
round 99, starting client 9/80, id: 8
Epoch [1/1], Train Loss: 0.0028196846643158305
round 99, starting client 10/80, id: 9
Epoch [1/1], Train Loss: 0.002096573915709828
round 99, starting client 11/80, id: 10
Epoch [1/1], Train Loss: 0.0023789647651331807
round 99, starting client 12/80, id: 11
Epoch [1/1], Train Loss: 0.0021990244904851637
round 99, startin

In [17]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd)

## 90

In [9]:
%%time
lstm_K5_gkd = copy.deepcopy(lstm)
outputs_gkd, targets_gkd, loss_gkd, smape_gkd, mae_gkd, rmse_gkd = fedgkd(
    global_model = lstm_K5_gkd,
    client_train_loader = train_loader,
    test_loader = test_loader,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
    buffer_size=buffer_size,
    kd_weight=kd_weight
)


Starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 0, starting client 1/90, id: 0


C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.06448793059812402
round 0, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.053922186129623
round 0, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.04640870101542936
round 0, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.051434575379186984
round 0, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.05814871471375226
round 0, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.052053420804440975
round 0, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.06281060816065685
round 0, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.051120131997005
round 0, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.055571520127929167
round 0, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.04660526394016213
round 0, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.06457159039564432
round 0, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.04043151041198718
round 0, starting client 13/90, id: 12
Epoch [1/1

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0548205256883828
round 1, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.04632871084743075
round 1, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.04210009107676644
round 1, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.04652367225464653
round 1, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.04968637719073078
round 1, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.04578735590912402
round 1, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.05304341828702269
round 1, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.04340884149215131
round 1, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.04902668429825169
round 1, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.040483590974299995
round 1, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.055441809662928186
round 1, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.0360407489597013
round 1, starting client 13/90, id: 12
Epoch [1/

...

Epoch [1/1], Train Loss: 0.0020542536853408472
round 97, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.002165645451491906
round 97, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.002437076739928064
round 97, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.002637561148160375
round 97, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.0023379029854285445
round 97, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.0023225879471283407
round 97, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.0021682093030068322
round 97, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.0016058634808462748
round 97, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.0029495422170909397
round 97, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.0021699329765936088
round 97, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.0024996961559130186
round 97, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.002246867650874743
round 97, startin

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020521270118891003
round 98, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.002162672096811649
round 98, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.002433884921224995
round 98, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.0026340766036061242
round 98, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.002334851459388368
round 98, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.0023195715111796744
round 98, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.002165635925012868
round 98, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.0016040439576894602
round 98, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.0029446513833066164
round 98, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.0021666548300008455
round 98, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.002496709843399003
round 98, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.0022438128086689265
round 98, starting

C:\Users\User\anaconda3\envs\fed\lib\site-packages\torch\nn\modules\loss.py:536: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1024, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch [1/1], Train Loss: 0.0020499947587388377
round 99, starting client 2/90, id: 1
Epoch [1/1], Train Loss: 0.002159741581676321
round 99, starting client 3/90, id: 2
Epoch [1/1], Train Loss: 0.002430372650754483
round 99, starting client 4/90, id: 3
Epoch [1/1], Train Loss: 0.002630664123560065
round 99, starting client 5/90, id: 4
Epoch [1/1], Train Loss: 0.002331798599863594
round 99, starting client 6/90, id: 5
Epoch [1/1], Train Loss: 0.0023168924977653655
round 99, starting client 7/90, id: 6
Epoch [1/1], Train Loss: 0.0021630521970675202
round 99, starting client 8/90, id: 7
Epoch [1/1], Train Loss: 0.0016021712239445097
round 99, starting client 9/90, id: 8
Epoch [1/1], Train Loss: 0.0029400110786529984
round 99, starting client 10/90, id: 9
Epoch [1/1], Train Loss: 0.00216349242934181
round 99, starting client 11/90, id: 10
Epoch [1/1], Train Loss: 0.0024935397620235267
round 99, starting client 12/90, id: 11
Epoch [1/1], Train Loss: 0.0022410734979386787
round 99, starting 

In [10]:
np.save(f'metrics/fedgkd_outputs_C{n_clients}.npy', np.array(outputs_gkd, dtype=object))
np.save(f'metrics/fedgkd_targets_C{n_clients}.npy', np.array(targets_gkd, dtype=object))
np.save(f'metrics/fedgkd_loss_C{n_clients}.npy', loss_gkd)
np.save(f'metrics/fedgkd_smape_C{n_clients}.npy', smape_gkd)
np.save(f'metrics/fedgkd_mae_C{n_clients}.npy', mae_gkd)
np.save(f'metrics/fedgkd_rmse_C{n_clients}.npy', rmse_gkd)